# Setting Up

In [1]:
!nvidia-smi

/bin/bash: nvidia-smi: command not found


In [2]:
!pip install pandas numpy scikit-learn matplotlib seaborn torch torchvision torchtext


In [3]:
#!pip install -q gradio torch

In [4]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
import joblib

In [5]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cpu')

In [6]:
import pandas as pd

df = pd.read_csv("/kaggle/input/drug-dataset/drug_dataset_big.csv")



#Data

In [7]:
df.head(5)

Drug Name  \
0                    abilify   
1                    actemra   
2                   afinitor   
3  alprazolam-ir-oral-tablet   
4     amlodipine-oral-tablet   

                                         Description  \
0  abilify\nabilify\nWhat is Abilify?\nIf you hav...   
1  actemra\nactemra\nWhat is Actemra?\nIf you hav...   
2  afinitor\nafinitor\nWhat is Afinitor?\nIf you ...   
3  alprazolam-ir-oral-tablet\nalprazolam-ir-oral-...   
4  amlodipine-oral-tablet\namlodipine-oral-tablet...   

                                                Uses  \
0  What is Abilify used for?\nIf you have a certa...   
1  What is Actemra used for?\nActemra is used to ...   
2  What is Afinitor used for?\nAfinitor and Afini...   
3  What is alprazolam IR oral tablet used for?\nI...   
4  What is amlodipine oral tablet used for?\nIf y...   

                                              Dosage  \
0  What is Abilify’s dosage?\nYour doctor will re...   
1  What is Actemra’s dosage?\nBelow are commonly ...   
2  What is Afinitor’s dosage?\nYour doctor will r...   
3  What is alprazolam’s dosage?\nYour doctor will...   
4  What is amlodipine oral tablet’s dosage?\nYour...   

                                        Side Effects  
0  What are Abilify’s side effects?\nLike most dr...  
1  What are Actemra’s side effects?\nLike most dr...  
2  What are Afinitor’s side effects?\nLike most d...  
3  What are alprazolam IR oral tablet’s side effe...  
4  What are amlodipine oral tablet’s side effects...

In [8]:
df.shape


(45898, 5)

In [9]:
# Iterate through columns and perform text cleaning
for column in df.columns:
    if df[column].dtype == 'object':  # Check if the column contains text
        df[column] = df[column].str.lower()

In [10]:
df.shape

(45898, 5)

In [11]:
# Drop rows with missing values
df = df.dropna().reset_index(drop=True)

In [12]:
df.shape

(45898, 5)

In [13]:
df.head()

Drug Name  \
0                    abilify   
1                    actemra   
2                   afinitor   
3  alprazolam-ir-oral-tablet   
4     amlodipine-oral-tablet   

                                         Description  \
0  abilify\nabilify\nwhat is abilify?\nif you hav...   
1  actemra\nactemra\nwhat is actemra?\nif you hav...   
2  afinitor\nafinitor\nwhat is afinitor?\nif you ...   
3  alprazolam-ir-oral-tablet\nalprazolam-ir-oral-...   
4  amlodipine-oral-tablet\namlodipine-oral-tablet...   

                                                Uses  \
0  what is abilify used for?\nif you have a certa...   
1  what is actemra used for?\nactemra is used to ...   
2  what is afinitor used for?\nafinitor and afini...   
3  what is alprazolam ir oral tablet used for?\ni...   
4  what is amlodipine oral tablet used for?\nif y...   

                                              Dosage  \
0  what is abilify’s dosage?\nyour doctor will re...   
1  what is actemra’s dosage?\nbelow are commonly ...   
2  what is afinitor’s dosage?\nyour doctor will r...   
3  what is alprazolam’s dosage?\nyour doctor will...   
4  what is amlodipine oral tablet’s dosage?\nyour...   

                                        Side Effects  
0  what are abilify’s side effects?\nlike most dr...  
1  what are actemra’s side effects?\nlike most dr...  
2  what are afinitor’s side effects?\nlike most d...  
3  what are alprazolam ir oral tablet’s side effe...  
4  what are amlodipine oral tablet’s side effects...

In [14]:
# Features & Labels
#X_features = df['Description']
#y_labels = df[['Drug Name', 'Uses', 'Dosage', 'Side Effects']]
X_features = df['Drug Name']
y_labels = df[['Uses', 'Dosage', 'Side Effects']]



In [15]:
from joblib import dump
from sklearn.preprocessing import LabelEncoder

In [16]:
df['Drug Name'].value_counts()

Drug Name
abilify                   30
ozempic                   30
soliqua                   30
sinemet                   30
rybrevant                 30
                          ..
etidronate                 4
etodolac                   4
etonogestrel               4
etonogestrel implant       4
zyvox (linezolid oral)     4
Name: count, Length: 10892, dtype: int64

In [17]:
#df['Description'].value_counts()

In [18]:
df['Uses'].value_counts()

Uses
acetaminophen is a pain reliever and fever reducer.                                                                                                                                                                                                                       340
salicylic acid is a keratolytic (peeling agent) that causes shedding of the outer layer of skin.                                                                                                                                                                          252
dextromethorphan is a cough suppressant. guaifenesin is an expectorant.                                                                                                                                                                                                   212
acetaminophen is a pain reliever and a fever reducer.                                                                                                                                    

In [19]:
df['Dosage'].value_counts()

Dosage
follow all directions on your prescription label and read all medication guides or instruction sheets. use the medicine exactly as directed.                                                   3360
follow all directions on your prescription label and read all medication guides or instruction sheets. your doctor may occasionally change your dose. use the medicine exactly as directed.    1484
use exactly as directed on the label, or as prescribed by your doctor.                                                                                                                         1440
use exactly as directed on the label, or as prescribed by your doctor. do not use in larger or smaller amounts or for longer than recommended.                                                 1200
use exactly as directed on the label, or as prescribed by your doctor. cold or cough medicine is only for short-term use until your symptoms clear up.                                          740
             

In [20]:
df['Side Effects'].value_counts()

Side Effects
along with its needed effects, a medicine may cause some unwanted effects. although not all of these side effects may occur, if they do occur they may need medical attention.                                                                                                 13836
get emergency medical help if you have signs of an allergic reaction: hives; difficult breathing; swelling of your face, lips, tongue, or throat.                                                                                                                              11424
get emergency medical help if you have signs of an allergic reaction: hives; difficulty breathing; swelling of your face, lips, tongue, or throat.                                                                                                                              2660
get emergency medical help if you have any of these signs of an allergic reaction: hives; difficult breathing; swelling of your face, lips, tongue, or throa

In [21]:
# Load Pkgs
from sklearn.multioutput import MultiOutputClassifier

In [22]:
# Features & Labels
Xfeatures = df['Drug Name']
ylabels = df[['Uses', 'Dosage', 'Side Effects']]

In [23]:
# Split Data
x_train,x_test,y_train,y_test = train_test_split(Xfeatures,ylabels,test_size=0.3,random_state=7)

from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.multioutput import MultiOutputClassifier
from sklearn.linear_model import LogisticRegression


pipe_lr = Pipeline(steps=[
    ('cv', CountVectorizer()),
    ('lr_multi', MultiOutputClassifier(LogisticRegression(max_iter=70)))  
])
# Fit on Dataset
pipe_lr.fit(x_train,y_train)

# Accuracy Score
pipe_lr.score(x_test,y_test)

# Sample Prediction
print(x_test.iloc[0])
print("Actual Prediction:",y_test.iloc[0])

ex1 = x_test.iloc[0]

pipe_lr.predict([ex1])

# Prediction Prob
print(pipe_lr.classes_)
pipe_lr.predict_proba([ex1])

# Save the trained model
model = 'drug_finder_3i.joblib'
dump(pipe_lr, model)
print("Model saved as", model)





/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/opt/conda/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _c

simply saline nasal
Actual Prediction: Uses            there are many brands and forms of sodium chlo...
Dosage          use exactly as directed on the label, or as pr...
Side Effects    get emergency medical help if you have signs o...
Name: 38463, dtype: object
[array(['13c urea and citric acid are medicines used in a diagnostic test called exalenz breathid® non-invasive breath test. it is a test that analyzes a breath sample before and after taking 13c-enriched urea to help diagnose patients with infections in the stomach caused by a bacteria called h. pylori.',
       'a-methapred is a steroid that prevents the release of substances in the body that cause inflammation.',
       'a-phedrin is a combination antihistamine and decongestant medicine that is used to treat runny or stuffy nose, sneezing, itching, watery eyes, and sinus congestion caused by allergies or the common cold.',
       ...,
       'zyrtec is used in adults and children to treat cold or allergy symptoms such as sn

#Define pipeline

In [24]:
# Sample Prediction
print(x_test.iloc[0])
print("Actual Prediction:",y_test.iloc[0])

simply saline nasal
Actual Prediction: Uses            there are many brands and forms of sodium chlo...
Dosage          use exactly as directed on the label, or as pr...
Side Effects    get emergency medical help if you have signs o...
Name: 38463, dtype: object


In [25]:
ex1 = x_test.iloc[0]

In [26]:
ex1

'simply saline nasal'

In [27]:
pipe_lr.predict([ex1])

array([['there are many brands and forms of sodium chloride nasal available. not all brands are listed on this leaflet.',
        'use exactly as directed on the label, or as prescribed by your doctor.',
        'get emergency medical help if you have signs of an allergic reaction: hives; difficult breathing; swelling of your face, lips, tongue, or throat.']],
      dtype=object)

In [28]:
# Prediction Prob
print(pipe_lr.classes_)
pipe_lr.predict_proba([ex1])

[array(['13c urea and citric acid are medicines used in a diagnostic test called exalenz breathid® non-invasive breath test. it is a test that analyzes a breath sample before and after taking 13c-enriched urea to help diagnose patients with infections in the stomach caused by a bacteria called h. pylori.',
       'a-methapred is a steroid that prevents the release of substances in the body that cause inflammation.',
       'a-phedrin is a combination antihistamine and decongestant medicine that is used to treat runny or stuffy nose, sneezing, itching, watery eyes, and sinus congestion caused by allergies or the common cold.',
       ...,
       'zyrtec is used in adults and children to treat cold or allergy symptoms such as sneezing, itching, watery eyes, or runny nose.',
       'zytiga works by reducing androgen production in the body. androgens are male hormones that can promote tumor growth in the prostate gland.',
       'zyvox is an oxazolidinone antibiotic that fights bacteria in

[array([[3.37608338e-05, 2.76920376e-05, 2.95217789e-05, ...,
         1.97527317e-05, 2.95217789e-05, 1.97613515e-05]]),
 array([[4.43886061e-05, 1.30972124e-05, 2.77455328e-05, ...,
         2.77514741e-05, 4.06287587e-05, 4.45356842e-05]]),
 array([[3.65662714e-06, 1.14434904e-05, 7.20965499e-06, ...,
         1.49463876e-05, 7.20965499e-06, 7.20965499e-06]])]

In [29]:
# Save the trained model
#model = 'drug_finder_big.joblib'
#dump(pipe_lr, model)
#print("Model saved as", model)

In [30]:
from joblib import load

# Load the saved model
loaded_model = load(model)


In [31]:
loaded_model.predict([ex1])

array([['there are many brands and forms of sodium chloride nasal available. not all brands are listed on this leaflet.',
        'use exactly as directed on the label, or as prescribed by your doctor.',
        'get emergency medical help if you have signs of an allergic reaction: hives; difficult breathing; swelling of your face, lips, tongue, or throat.']],
      dtype=object)

In [32]:
# Sample prediction
sample_input = [ex1]

# Predict probabilities for each class in each output
prediction_probs = loaded_model.predict_proba(sample_input)

# Print the predicted probabilities
print("Prediction Probabilities:")
print(prediction_probs)

Prediction Probabilities:
[array([[3.37608338e-05, 2.76920376e-05, 2.95217789e-05, ...,
        1.97527317e-05, 2.95217789e-05, 1.97613515e-05]]), array([[4.43886061e-05, 1.30972124e-05, 2.77455328e-05, ...,
        2.77514741e-05, 4.06287587e-05, 4.45356842e-05]]), array([[3.65662714e-06, 1.14434904e-05, 7.20965499e-06, ...,
        1.49463876e-05, 7.20965499e-06, 7.20965499e-06]])]


###Using ML Estimators KNN which supports multi-output

In [33]:
from sklearn.pipeline import Pipeline
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.neighbors import KNeighborsClassifier

# Define your pipeline
pipe_knn = Pipeline(steps=[
    ('cv', CountVectorizer()),
    ('knn', KNeighborsClassifier(n_neighbors=4))
])


In [34]:
pipe_knn.fit(x_train,y_train)

Pipeline(steps=[('cv', CountVectorizer()),
                ('knn', KNeighborsClassifier(n_neighbors=4))])

In [35]:
# Save the trained model
model = 'drug_finder_3i_knn.joblib'
dump(pipe_knn, model)
print("Model saved as", model)


Model saved as drug_finder_3i_knn.joblib


In [36]:
from joblib import load

# Load the saved model
loaded_model = load(model)


In [37]:
loaded_model.predict([ex1])

array([['there are many brands and forms of sodium chloride nasal available. not all brands are listed on this leaflet.',
        'use exactly as directed on the label, or as prescribed by your doctor.',
        'get emergency medical help if you have signs of an allergic reaction: hives; difficult breathing; swelling of your face, lips, tongue, or throat.']],
      dtype=object)

In [38]:
# Sample prediction
sample_input = [ex1]

# Predict probabilities for each class in each output
prediction_probs = loaded_model.predict_proba(sample_input)

# Print the predicted probabilities
print("Prediction Probabilities:")
print(prediction_probs)


Prediction Probabilities:
[array([[0., 0., 0., ..., 0., 0., 0.]]), array([[0., 0., 0., ..., 0., 0., 0.]]), array([[0., 0., 0., ..., 0., 0., 0.]])]


In [39]:
Pipeline(steps=[('cv', CountVectorizer()),
                ('knn', KNeighborsClassifier(n_neighbors=4))])

Pipeline(steps=[('cv', CountVectorizer()),
                ('knn', KNeighborsClassifier(n_neighbors=4))])

In [40]:
pipe_knn.predict([ex1])

array([['there are many brands and forms of sodium chloride nasal available. not all brands are listed on this leaflet.',
        'use exactly as directed on the label, or as prescribed by your doctor.',
        'get emergency medical help if you have signs of an allergic reaction: hives; difficult breathing; swelling of your face, lips, tongue, or throat.']],
      dtype=object)